# Download, busca e cópia de Arquivos XML do Diário Oficial - Extração das publicações do Ministério da Defesa

#### O presente script tem como intuito padronizar o texto presente no Diário da União afim de transforma-lo em uma base de dados

- Os diários da união, anteriores a 2020 podem ser encontrados em formato .zip pelo site da Imprensa Nacional: https://in.gov.br/dados-abertos/base-de-dados/publicacoes-do-dou
- O recorte temporal da extração desse script será das publicações entre **2001 e 2020**, visto que após 2020 a coleta de dados será feita de outra forma, a fim de automatizar a extração para que alimente a base de dados diariamente;
- Visando uma robustez, optou-se pelo download manual dos diários;
- OBS: O diário da união de janeiro de 2006 não esta disponivel pelo site da imprensa; e também feveiro de 2004 https://in.gov.br/dados-abertos/base-de-dados/publicacoes-do-dou/2020/novembro
- Até 2020 os dados por meio dos arquivos zipados existem, depois de 2020 não existem mais.

**Download dos Pacotes**

In [96]:
import os
import shutil
import xml.etree.ElementTree as ET
import re
import pandas as pd
import openpyxl
from geonamescache import GeonamesCache
import spacy
from spacy import displacy

**Direcionamento do diretório com os arquivos do Diário da União**

In [2]:
# Pasta contendo os arquivos XML
pasta_base = "C:/Users/paula/OneDrive/IPEA/Militares_2/"
pasta_diario_uniao = os.path.join(pasta_base, "diario_uniao")
pasta_militares = os.path.join(pasta_base, "diario_uniao_militares")

**Função que filtra os arquivos contendo "Ministério da Defesa" como string**

In [3]:
# Função para encontrar os arquivos com a especificação desejada
def encontrar_arquivos_especificos(pasta, string_procurada):
    arquivos_encontrados = []
    for root, dirs, _ in os.walk(pasta):
        for dir in dirs:
            ano = os.path.basename(root)
            mes = dir
            pasta_mes = os.path.join(root, mes)
            for arquivo in os.listdir(pasta_mes):
                if arquivo.endswith(".xml"):
                    caminho_arquivo = os.path.join(pasta_mes, arquivo)
                    try:
                        tree = ET.parse(caminho_arquivo)
                        elemento_raiz = tree.getroot()
                        for article in elemento_raiz.findall('.//article'):
                            if 'artCategory' in article.attrib:
                                if string_procurada.lower() in article.attrib['artCategory'].lower():
                                    arquivos_encontrados.append((caminho_arquivo, ano, mes))
                                    print(f"Publicação pertencente ao Ministério da Defesa: {arquivo}")
                                    break
                    except ET.ParseError:
                        print(f"Erro ao analisar o arquivo XML: {arquivo}")
    return arquivos_encontrados

**Arquivos com a especificação desejada**

In [ ]:
# String procurada
string_procurada = "Ministério da Defesa/"

# Print dos arquivos encontrados
arquivos_encontrados = encontrar_arquivos_especificos(pasta_diario_uniao, string_procurada)

Erro ao analisar o arquivo XML: 22002010210.xml
Publicação pertencente ao Ministério da Defesa: 22002010211.xml
Publicação pertencente ao Ministério da Defesa: 22002010212.xml
Publicação pertencente ao Ministério da Defesa: 22002010213.xml
Publicação pertencente ao Ministério da Defesa: 22002010214.xml
Publicação pertencente ao Ministério da Defesa: 22002010215.xml
Publicação pertencente ao Ministério da Defesa: 22002010216.xml
Erro ao analisar o arquivo XML: 22002010240.xml
Publicação pertencente ao Ministério da Defesa: 2200201025.xml
Publicação pertencente ao Ministério da Defesa: 2200201026.xml
Erro ao analisar o arquivo XML: 22002010260.xml
Publicação pertencente ao Ministério da Defesa: 2200201027.xml
Publicação pertencente ao Ministério da Defesa: 2200201028.xml
Publicação pertencente ao Ministério da Defesa: 2200201029.xml
Erro ao analisar o arquivo XML: 2200201031.xml
Publicação pertencente ao Ministério da Defesa: 22002010311.xml
Publicação pertencente ao Ministério da Defesa

In [ ]:
# Criar a pasta 'diario_uniao_militares' se ela ainda não existir
if not os.path.exists(pasta_militares):
    os.makedirs(pasta_militares)

In [ ]:
# Mover os arquivos encontrados para a pasta 'diario_uniao_militares'
for arquivo, ano, mes in arquivos_encontrados:
    destino = os.path.join(pasta_militares, ano, mes)
    os.makedirs(destino, exist_ok=True)
    shutil.copy(arquivo, destino)
print(f"Total de {len(arquivos_encontrados)} arquivos movidos para '{pasta_militares}'.")

Total de 151288 arquivos movidos para 'C:/Users/paula/OneDrive/IPEA/Militares_2/diario_uniao_militares'.


- ## Filtrar os dados para as publicações que possuam "afastamento", "afastar-se" e "missão"

In [29]:
# Pasta contendo os arquivos XML
pasta_base = "C:/Users/paula/OneDrive/IPEA/Militares_2/diario_uniao_militares"

# Pasta para salvar os arquivos correspondentes
pasta_destino = "C:/Users/paula/OneDrive/IPEA/Militares_2/diario_uniao_militares_afastamentos"

# Palavras-chave a serem procuradas nos arquivos XML
palavras_chave = ["afastamento", "afastar-se", "missão"]

In [30]:
# Função para verificar se o arquivo contém as palavras-chave
def copiar_arquivos_com_palavras_chave(pasta, palavras_chave):
    arquivos_encontrados = []
    for root, dirs, _ in os.walk(pasta):
        for dir in dirs:
            ano = os.path.basename(root)
            mes = dir
            pasta_mes = os.path.join(root, mes)
            for arquivo in os.listdir(pasta_mes):
                if arquivo.endswith(".xml"):
                    caminho_arquivo = os.path.join(pasta_mes, arquivo)
                    try:
                        tree = ET.parse(caminho_arquivo)
                        elemento_raiz = tree.getroot()
                        for article in elemento_raiz.findall('.//article'):
                            for palavra_chave in palavras_chave:
                                if palavra_chave.lower() in ET.tostring(article).lower().decode("utf-8"):
                                    arquivos_encontrados.append((caminho_arquivo, ano, mes))
                                    print(f"Encontrado em: {arquivo}")
                                    break
                    except ET.ParseError:
                        print(f"Erro ao analisar o arquivo XML: {arquivo}")
    return arquivos_encontrados

In [31]:
# Verificar se a pasta de destino existe, senão criar
if not os.path.exists(pasta_destino):
    os.makedirs(pasta_destino)

In [32]:
# Verificar e mover os arquivos XML
def copiar_arquivos_com_palavras_chave(pasta_base, pasta_destino, palavras_chave):
    arquivos_copiados = 0
    
    for pasta_raiz, _, arquivos in os.walk(pasta_base):
        for arquivo in arquivos:
            caminho_arquivo = os.path.join(pasta_raiz, arquivo)
            if contem_palavras_chave(caminho_arquivo, palavras_chave):
                # Calcular o caminho relativo do arquivo em relação à pasta base
                caminho_relativo = os.path.relpath(pasta_raiz, pasta_base)
                
                # Criar a estrutura de pastas no destino se necessário
                pasta_destino_completa = os.path.join(pasta_destino, caminho_relativo)
                os.makedirs(pasta_destino_completa, exist_ok=True)
                
                # Copiar o arquivo para o destino
                destino_arquivo = os.path.join(pasta_destino_completa, arquivo)
                shutil.copy(caminho_arquivo, destino_arquivo)
                arquivos_copiados += 1
                
    print(f"Total de {arquivos_copiados} arquivos XML copiados para a pasta {pasta_destino}.")

In [33]:
# Chame a função para copiar os arquivos
copiar_arquivos_com_palavras_chave(pasta_base, pasta_destino, palavras_chave)

Total de 12932 arquivos XML copiados para a pasta C:/Users/paula/OneDrive/IPEA/Militares_2/diario_uniao_militares_afastamentos.


- ## Estruturação da Base de Dados dos Diários Extraídos em arquivo xlsx 

In [89]:
#Função de Estruturação do DATAFRAME
def extrair_dados_xml(caminho_arquivo):
    try:
        tree = ET.parse(caminho_arquivo)
        elemento_raiz = tree.getroot()
        
        # Extrair dados do XML
        body = elemento_raiz.find('.//body')
        identifica = body.find('.//Identifica').text if (body is not None and body.find('.//Identifica') is not None) else ''
        texto = body.find('.//Texto').text if (body is not None and body.find('.//Texto') is not None) else ''

        # Extrair atributos do elemento article
        article_attribs = elemento_raiz.find('.//article').attrib

        # Atributos a serem excluídos
        atributos_excluir = ['Number Page', 'Publicação Name', 'Art Type', 'Publicação Date', 'Art Category']

        # Remover atributos indesejados
        for atributo in atributos_excluir:
            article_attribs.pop(atributo, None)

        # Adicionar dados ao dicionário
        dados = {
            'Identifica': identifica,
            'Texto': texto,
        }

        # Adicionar atributos do elemento article ao dicionário
        dados.update(article_attribs)

        return dados
    except ET.ParseError as e:
        print(f"Erro ao analisar o arquivo XML '{caminho_arquivo}': {e}")
        return None

In [90]:
#Função para pegar os arquivos das pastas
def criar_dataframe_com_dados(pasta_base):
    dados = []
    for root, _, arquivos in os.walk(pasta_base):
        for arquivo in arquivos:
            if arquivo.endswith(".xml"):
                caminho_arquivo = os.path.join(root, arquivo)
                dados_xml = extrair_dados_xml(caminho_arquivo)
                if dados_xml:
                    dados.append(dados_xml)

    df = pd.DataFrame(dados)
    return df

In [91]:
# Pasta base onde estão os arquivos XML
pasta_base = "C:/Users/paula/OneDrive/IPEA/Militares_2/diario_uniao_militares_afastamentos"

In [92]:
# DataFrame com os dados dos arquivos XML
df = criar_dataframe_com_dados(pasta_base)

In [93]:
# Salve o DataFrame em um arquivo Excel
caminho_arquivo_excel = "dados_diario_uniao_militares_afastamentos.xlsx"
df.to_excel(caminho_arquivo_excel, index=False)

# Imprima a quantidade de linhas do DataFrame
print(f"Quantidade de linhas no DataFrame: {len(df)}")

Quantidade de linhas no DataFrame: 12932


- ## Limpeza da Base de Dados para extrair país, cidade, tipo de afastamento, patente e período de afastamento. 

In [98]:
# Função para extrair informações do texto
# PAÍS 
# Carregar o modelo de PLN pré-treinado do spaCy para português
nlp = spacy.load("pt_core_news_sm")
# Carregar o arquivo xlsx
df = pd.read_excel('dados_diario_uniao_militares_afastamentos_paises_teste.xlsx')

In [99]:
# Função para extrair entidades de um texto usando spaCy
def extrair_entidades(texto):
    doc = nlp(texto)
    entidades = [(ent.text, ent.label_) for ent in doc.ents]
    return entidades

In [100]:
# Iterar sobre as entidades na coluna "Texto" do DataFrame
for indice, linha in df.iterrows():
    texto = linha['Texto']
    entidades_texto = extrair_entidades(texto)
    print(f"Entidades no texto {indice}: {entidades_texto}")

Entidades no texto 0: [("class='identifica", 'ORG'), ('DEZEMBRO', 'MISC'), ("class='corpo", 'MISC'), ('COMANDANTE', 'ORG'), ('MARINHA', 'ORG'), ('Decreto', 'LOC'), ('Lei Complementar', 'MISC'), ("class='corpo", 'MISC'), ('Art. 1o Alterar', 'MISC'), ('Portarias', 'LOC'), ("class='corpo", 'MISC'), ('§', 'ORG'), ('Portaria', 'MISC'), ('D.O.U.', 'ORG'), ('Seção 2', 'MISC'), ('Primeiro-Tenente CLAUDIO', 'MISC'), ('exterior.</p', 'LOC'), ("class='corpo", 'MISC'), ('§', 'ORG'), ('Portaria', 'MISC'), ('D.O.U.', 'ORG'), ('Seção 2', 'MISC'), ('Primeiro-Tenente', 'LOC'), ('ADRIANO PIRES', 'PER'), ('CRUZ', 'ORG'), ('exterior.</p', 'LOC'), ("class='corpo", 'MISC'), ('§', 'ORG'), ('Portaria', 'MISC'), ('D.O.U.', 'ORG'), ('Seção 2', 'MISC'), ('Primeiro-Tenente', 'LOC'), ('LEANDRO', 'MISC'), ('exterior.</p', 'LOC'), ("class='corpo", 'MISC'), ('Art. 2o', 'MISC'), ('propõe.</p', 'LOC'), ("class='assina", 'ORG'), ('G. F. CHAGASTELES', 'PER')]
Entidades no texto 1: [("class='identifica", 'ORG'), ("class='

In [101]:
# Iterar sobre as entidades na coluna "Texto" do DataFrame
def extrair_entidades(texto):
    doc = nlp(texto)
    return doc

In [102]:
for indice, linha in df.iterrows():
    texto = linha['Texto']
    doc = extrair_entidades(texto)
    displacy.render(doc, style="ent", jupyter=True)

In [ ]:
TRAIN_DATA = [
    ("o Capitão-de-Mar-e-Guerra DOUGLAS ARAÚJO ALVES, para exercer o cargo de Adido Naval junto à Embaixada do Brasil na Venezuela, com sede em Caracas;",
     {"entities": [(27, 52, "PER")]}),
    ("o Capitão-de-Mar-e-Guerra PAULO MAURICIO FARIAS ALVES, para exercer o cargo de Adido Naval junto à Embaixada do Brasil na Itália, com sede em Roma;",
     {"entities": [(27, 55, "PER"), (4, 29, "MISC")]}),
    ("NOMEAR, por necessidade do serviço, o Suboficial BCT PAULO EUGENIO ECHEVARRIA (4º/1º GCC / NO 2352290) para o cargo de Auxiliar da Assessoria de Proteção ao Voo na Missão Técnica Aeronáutica Brasileira, em Assunção, República do Paraguai, de acordo com as datas abaixo relacionadas:",
     {"entities": [(39, 68, "PER"), (16, 32, "MISC")]}),
    ("Designar o Contra-Almirante (Md) LUIZ CLAUDIO BARBEDO FRÓES, Diretor do Departamento de Saúde e Assistência Social do Ministério da Defesa (DESAS/MD), e o Coronel Médico LUCAS VILHENA DE MORAES, Gerente da Divisão de Saúde (DISAU/DESAS/MD), para participarem do 8º Congresso Regional do Grupo de Trabalho Regional Pan-Americano e Assembleia Regional do Comitê Internacional de Medicina Militar (CIMM), a serem realizados no período de 7 a 9 de novembro de 2016, na Cidade do México - México.",
     {"entities": [(22, 59, "PER"), (60, 115, "PER"), (144, 187, "MISC"), (217, 272, "MISC"), (282, 297, "LOC"), (301, 307, "LOC")]}),
    ("AUTORIZAR o afastamento do País do Brigadeiro do Ar TARCÍSIO DE AQUINO BRITO VELOSO - Subchefe de Logística Operacional do Estado-Maior Conjunto das Forças Armadas, para compor comitiva ministerial em viagem às cidades de Beirute e Naqoura, República do Líbano, no período de 31 de outubro a 05 de novembro de 2016, incluindo o trânsito, com ônus para o Ministério da Defesa.",
     {"entities": [(37, 71, "PER"), (23, 40, "MISC"), (89, 105, "LOC"), (110, 117, "LOC")]}),
    ("AUTORIZAR, o afastamento do País da Capitão de Corveta (T) CAMILA DA SILVA NETO ARRUDA - Ajudante de Ordens do Ministro de Estado da Defesa, para compor comitiva ministerial em viagem às cidades de Beirute e Naqoura, República do Líbano, no período de 31 de outubro a 05 de novembro de 2016, incluindo o trânsito, com ônus para o Ministério da Defesa.",
     {"entities": [(35, 67, "PER"), (19, 41, "MISC"), (89, 105, "LOC"), (110, 117, "LOC")]}),
    ("AUTORIZAR,o afastamento do País da Capitão de Corveta (T) CAMILA DA SILVA NETO ARRUDA - Ajudante de Ordens do Ministro de Estado da Defesa, para compor comitiva ministerial em viagem às cidades de Beirute e Naqoura, República do Líbano, no período de 31 de outubro a 05 de novembro de 2016, incluindo o trânsito, com ônus para o Ministério da Defesa.",
     {"entities": [(37, 69, "PER"), (21, 43, "MISC"), (91, 107, "LOC"), (112, 119, "LOC")]}),
    ("Autorizar o Ten Cel Inf CHARLES ROBERTO MARTINS DA SILVA a realizar o Curso de Planejamento de Movimento Internacional no Centro Internacional de Defesa da Noruega (NORDEFCO International Movement Planning Course), em Oslo - Noruega, no período de 5 a 19 de novembro de 2016, incluindo o trânsito, com ônus total para o Ministério da Defesa.",
     {"entities": [(10, 34, "PER"), (3, 13, "MISC"), (37, 193, "MISC"), (198, 203, "LOC"), (207, 214, "LOC")]}),
    ("Designar os militares abaixo relacionados para a seguinte missão no exterior: Capitão de Fragata (FN) CARLOS FREDERICO WERNER (Encarregado); Capitão-Tenente (AFN) ARILSON DE OLIVEIRA SILVA (Auxiliar); SO-FN-IF 86.3208.58 DORIEDSON MARTINS DE SOUZA; SO-FN-IF 85.3939.08 OSVALDO MARTINS VAQUEIRO; SO-FN-IF 85.0055.50 PAULO ANTONIO DA SILVA RODRIGUES; 1ºSG-FN-IF 86.9296.31 DAVI BEZERRIL DE SOUZA; 1ºSG-FN-IF 87.1602.34 KLERTON MORAES DE OLIVEIRA; 1ºSG-FN-CN 87.1613.03 MARCELIO ALVES DE AGUIAR; e 1ºSG-FN-MO 87.2342.46 SAMUEL RODRIGUES PAES LEME FILHO. Missão - Realizar intercâmbio compondo o Grupo de Assessoramento Técnico de Fuzileiros Navais (GAT-FN) junto à Guarda Costeira de São Tomé e Príncipe. Local - São Tomé e Príncipe. Período - de 15 de fevereiro de 2017 a 26 de fevereiro de 2018, podendo se ausentar do País a partir do dia 2 de fevereiro de 2017 e retornar ao País até o dia 31 de março de 2018.",
     {"entities": [(54, 90, "MISC"), (96, 132, "MISC"), (145, 177, "MISC"), (178, 209, "MISC"), (210, 245, "MISC"), (246, 279, "MISC"), (280, 314, "MISC"), (315, 349, "MISC"), (350, 396, "MISC"), (401, 446, "LOC")]}),
    ("Art. 1º Designar o Capitão de Fragata ERNESTO SERRANO RODRIGUEZ FILHO para a seguinte missão no exterior: Missão - Acompanhar a equipe do Projeto 'Antártica por um ano' durante a OPERANTAR XXXV. Local - Punta Arenas (Chile) e Antártica, a bordo do NApOcARongel e alojado na EAComteFerraz.",
     {"entities": [(27, 45, "MISC"), (46, 84, "PER"), (95, 169, "MISC"), (175, 187, "LOC"), (191, 227, "LOC")]}),
]

In [ ]:
TRAIN_DATA = [
    ("NOMEAR, por necessidade do serviço, o Suboficial BCT PAULO EUGENIO ECHEVARRIA (4º/1º GCC / NO 2352290) para o cargo de Auxiliar da Assessoria de Proteção ao Voo na Missão Técnica Aeronáutica Brasileira, em Assunção, República do Paraguai, de acordo com as datas abaixo relacionadas:",
     {"entities": [(0, 5, "AÇÃO"),
                   (38, 47, "PATENTE"),
                   (49, 76, "PER"),
                   (119, 152, "CARGO"),
                   (206, 2013, "LOC_CIDADE"),
                   (216, 236, "LOC_PAIS")]}), # 1 inserção
    ("Designar os militares abaixo relacionados para realizarem missão no exterior: Capitão de Mar e Guerra (RM1-IM) PAOLO STANZIOLA NETO; Capitão de Mar e Guerra (RM1-T) ALEXANDRE KUHNERT DOURADO; Capitão-Tenente (A-FN) RAIMUNDO NONATO MACIEL DA SILVA; SO-ES 86.7969.17 MARCO ROBERTO MARTINS; SO-MT 85.8919.91 EDSON DOS SANTOS; 1ºSG-MO 95.1021.24 MARCIO CASTRO VIEIRA; 2ºSG-CN 97.1156.14 MARCOS ANTONIO DA SILVA PEREIRA; 2ºSG-PL 97.1126.31 JORGE FERREIRA MARQUES DOS SANTOS; CB-CL 12.1390.25 MARIA APARECIDA CASTRO DOS SANTOS; CB-RM1-AR 82.1254.49 ANTONIO CLAUDIO AFFONSO DA SILVA; MN-RM2 11.1277.16 PAULO HENRIQUE RIBEIROS DOS SANTOS; e MN-RM2 11.1282.83 JOSÉ FLÁVIO ANANIAS GOMES. Participar do 2º Voo de Apoio Logístico à OPERANTAR XXXV para o transporte de pessoal e de material, objetivando prestar apoio logístico à Estação Antártica Comandante Ferraz. Punta Arenas (Chile) e Antártica.", 
     {"entities": [
         (0, 7, "AÇÃO"), 
         (78, 100, "PATENTE"), (111, 130, "PER"), 
         (133, 155, "PATENTE"), (165, 189, "PER"), 
         (192, 206, "PATENTE"), (215, 245, "PER"), 
         (248, 252, "PATENTE"), (265, 285, "PER"), 
         (288, 292, "PATENTE"), (305, 320, "PER"), 
         (323, 329, "PATENTE"), (342, 361, "PER"), 
         (364, 370, "PATENTE"), (383, 413, "PER"), 
         (416, 422, "PATENTE"), (435, 467, "PER"), 
         (470, 474, "PATENTE"), (487, 519, "PER"), 
         (522, 530, "PATENTE"), (543, 574, "PER"), 
         (577, 582, "PATENTE"), (595, 628, "PER"), 
         (633, 638, "PATENTE"), (651, 675, "PER"), 
         (692, 733, "EVENTO"),
         (854,865, "LOC_CIDADE"), 
         (868,872, "LOC_PAIS"), 
         (877,885, "LOC_REGIAO")
     ]}), # 2 inserção
    ("Art. 1º Autorizar o afastamento do País da Servidora Civil NI-S-III, DAS-102.2, 03.7212.72 EDNA FRANCISCA DE ARAÚJO PEREIRA, Matrícula SIAPE nº 0957775 para a seguinte missão no exterior: Missão - Participar do 2º Voo de Apoio Logístico à OPERANTAR XXXV para o transporte de pessoal e de material, objetivando prestar apoio logístico à Estação Antártica Comandante Ferraz. Locais - Punta Arenas (Chile) e Antártica.",
     {"entities": [
         (8,16, "AÇÃO"),  # Autorizar
         (43,57, "PATENTE"),  # Servidora Civil
         (91,122, "PER"),  # EDNA FRANCISCA DE ARAÚJO PEREIRA
         (197,252, "EVENTO"),  # Participar do 2º Voo de Apoio Logístico à OPERANTAR XXXV
         (382,393, "LOC_CIDADE"),  # Punta Arenas
         (396,400, "LOC_PAIS"),  # Chile
         (405,413, "LOC_REGIAO")  # Antártica
     ]}), # 3 inserção
    ("Art. 1o Designar o Capitão-de-Mar-e-Guerra LUIZ CARLOS PINHEIRO SERRANO para participar do Simpósio Internacional/2008 do Conselho Internacional do Esporte Militar, a realizar-se na cidade de Sofia - Bulgária, no período de 23 a 27 de setembro de 2008.",
     {"entities": [(8,15, "AÇÃO"), (19,41, "PATENTE"), (43,70, "PER"), (91,162, "EVENTO"), (192,196, "LOC_CIDADE"), (200,207, "LOC_PAIS")]}), # 4 inserção
   ("Designar o Coronel FLAVIO MARCONDES JUNIOR para participar da 3ª Reunião do Quadro de Diretores do Conselho Internacional do Esporte Militar, a realizar-se na cidade de Tunis - Tunísia, no período de 19 a 25 de outubro de 2008.",
     {"entities": [
         (0,7, "AÇÃO"),  # Designar
         (11,17, "PATENTE"),  # Coronel
         (19,41, "PER"),  # FLAVIO MARCONDES JUNIOR
         (62,139, "EVENTO"),  # 3ª Reunião do Quadro de Diretores do Conselho Internacional do Esporte Militar
         (169,173, "LOC_CIDADE"),  # Tunis
         (177,183, "LOC_PAIS"),  # Tunísia
     ]}), # 4 inserção
    ("Nº284-Art. 1º Designar os oficiais abaixo relacionados para realizar a seguinte missão no exterior: Capitão-de-Mar-e-Guerra (FN) RAIMUNDO LOPES CAMARGOS FILHO; Capitão-de-Mar-e-Guerra (FN) CARLOS ROBERTO DE ALMEIDA BASTOS; Capitão-de-Mar-e-Guerra (FN) SERGIO CHAVES DE JESUS; Capitão-de-Mar-e-Guerra (FN-RM1) JOSÉ CARLOS LINARES BASTOS; Capitão-de-Fragata (FN) LINO CESAR PESTANA GOMES; e Capitão-de-Fragata LUIZ FERNANDO DA SILVA BEZERRA. Missão - Participar da Viagem de Avaliação do Desempenho da Tropa no Haiti, coordenada pelo Ministério da Defesa. Local - Porto Príncipe - Haiti.", 
     {"entities": [(14, 21, "ACAO"),
                   (100, 122, "PATENTE"),
                   (129, 157, "PER"),
                   (160,182, "PATENTE"),
                   (189,220, "PER"),
                   (223,245, "PATENTE"),
                   (252,273, "PER"),
                   (276,298, "PATENTE"),
                   (309,334, "PER"),
                   (337,354, "PATENTE"),
                   (361,384, "PER"),
                   (389,406, "PATENTE"),
                   (408,437, "PER"),
                   (463,513, "EVENTO"),
                   (527, 542, "562,575"),
                   (579,583, "LOC_PAIS")]}), # 5 inserção
    ("A DIRETORA-PRESIDENTE DA AGÊNCIA NACIONAL DE AVIAÇÃO CIVIL - ANAC, no uso das atribuições que lhe conferem o art. 16 da Lei no 11.182, de 27 de setembro de 2005, e o art. 10 do Anexo da Resolução nº 38, de 07 de agosto de 2008, autoriza o afastamento do País, com ônus, no período de 20 a 25 de outubro de 2008, incluindo trânsito, do Ten. Cel. Av. ROGÉRIO FANIN, a fim de realizar avaliação de proficiência técnica em simulador de vôo no equipamento EC55, dos pilotos Marcelo Kazakevicius, CANAC 846881 e Álvaro Stamato Sandoval, CANAC 531731, da Empresa Ocean Explorer do Brasil Ltda., na cidade de Marseille - França, conforme o Processo nº 60840.012539/2008-15.", 
     {"entities": [(228,235, "AÇÃO"),
                   (335,347, "PATENTE"),
                   (349,361, "PER"),
                   (382,454, "EVENTO"),
                   (601,609, "LOC_CIDADE"), 
                   (613,618, "LOC_PAIS")]}) # 6 inserção
]